## Get measurements

In [6]:
import pickle
from copy import deepcopy

from collections import defaultdict

anchors_file = "../datasets/anchors.pickle"
anchors_measurement_file = "../results/anchors_to_anchors_measurements.pickle"

with open(anchors_file, "rb") as f:
    anchors = pickle.load(f)

# load already existing measurements
with open(anchors_measurement_file, "rb") as f:
    anchor_measurements = pickle.load(f)


# sfor debugging, print some results
filtered_results = deepcopy(anchor_measurements)
for i, anchor in enumerate(filtered_results):
    if i > 10: break
    print(f"target ip: {anchor}, number of measurements: {len(anchor_measurements[anchor]['result'][0])}")
    
with open(anchors_measurement_file, "wb") as f:
    pickle.dump(anchor_measurements, f)

target ip: 129.13.73.54, number of measurements: 775
target ip: 152.195.112.52, number of measurements: 775
target ip: 193.46.104.17, number of measurements: 772
target ip: 200.3.170.54, number of measurements: 775
target ip: 195.30.70.33, number of measurements: 775
target ip: 86.38.3.141, number of measurements: 769
target ip: 77.110.218.255, number of measurements: 774
target ip: 156.154.135.254, number of measurements: 772
target ip: 34.89.240.90, number of measurements: 766
target ip: 34.68.239.153, number of measurements: 767
target ip: 195.130.66.103, number of measurements: 774


## select dataset

In [9]:
from random import choice

NB_TARGET = 1_00 # testing
NB_VP = 1 # testing

# select targets and vps from anchors
targets= [choice(list(anchor_measurements)) for _ in range(0, NB_TARGET)]
vps = list(set(anchor_measurements).difference(set(targets)))

analysis_dataset = {}
for i, target_addr in enumerate(targets):

    # select measurement where source is in vps
    measurement_results = []
    for result in anchor_measurements[target_addr]['result'][0]:

        if result['node'] in vps:
            measurement_results.append(result)
        
    analysis_dataset[target_addr] = measurement_results

## analyze data

In [14]:
from pathlib import Path
import pickle
from copy import copy

from geoloc_imc_2023.helpers import polygon_centroid, haversine, circle_intersections
from geoloc_imc_2023.draw_results import draw_results

def select_best_guess_centroid(target_addr, measurement_results):
    """
    Find the best guess
    that is the location of the vantage point closest to the centroid.
    """
    probe_circles = {}
    print(f"NUMBER OF MEASUREMENT RESULTS FOR TARGET IP: {target_addr} : {len(measurement_results)}")
    for _, result in enumerate(measurement_results):
        vp_ip = result["node"]
        lat = result["vp_lat"]
        lon = result["vp_lon"]
        min_rtt = result["min_rtt"]

        # too inflated RTT means that measurement will not provide usefull info
        if isinstance(min_rtt, float):
                probe_circles[vp_ip] = (
                    lat,
                    lon,
                    min_rtt,
                    None,
                    None,
                )
                print(f"vp_anchor = {vp_ip} with results: {min_rtt}")
    print()

    # draw circles
    if not probe_circles: return

    intersections = circle_intersections(probe_circles.values(), speed_threshold=4/9)
    print("intersecion:", intersections)
    target = (anchors[target_addr]["latitude"], anchors[target_addr]["longitude"])

    centroid = None
    if intersections:
        centroid = polygon_centroid(intersections)
        print("centroid:", centroid)
        target_description = anchors[target_addr]

        if centroid:
            for ip_src, circle in probe_circles.items():

                measured_d = haversine((circle[0], circle[1]), centroid)
                calculated_d = haversine((target_description["latitude"], target_description["longitude"]), centroid)

                print("ip_src:",ip_src,"dst (measured):", measured_d, "dst (calculated):", calculated_d)
    
    draw_results(copy(probe_circles), intersections,centroid, target)

    return centroid

anchor_file = "../datasets/anchors.pickle"
with open(anchor_file, "rb") as f:
    anchors = pickle.load(f)

geoloc_results = {}
for i, target_addr in enumerate(analysis_dataset):
    if i > 15: break

    print("available measurements for ip:",len(analysis_dataset[target_addr]))

    shortest_delay_results = analysis_dataset[target_addr][:20]
    print(shortest_delay_results)

    centroid = select_best_guess_centroid(target_addr, shortest_delay_results)
    if centroid:
        geoloc_results[target_addr] = {
            "estimated_lat": centroid[0],
            "estimated_lon": centroid[1],
        }

geoloc_out_file = Path(".") / "../results/all_anchors_towards_all_anchors_geoloc.pickle"
with open(geoloc_out_file, "wb") as f:
    pickle.dump(geoloc_results, f)

available measurements for ip: 685
[{'node': '83.243.44.55', 'min_rtt': 0.607207, 'rtt_list': [1.744995, 0.607207, 1.703945], 'vp_lat': 50.1385, 'vp_lon': 8.7375}, {'node': '45.76.86.163', 'min_rtt': 0.679369, 'rtt_list': [0.770752, 0.679369, 3.324455], 'vp_lat': 50.1175, 'vp_lon': 8.7405}, {'node': '156.154.76.254', 'min_rtt': 0.766842, 'rtt_list': [8.814877, 0.766842, 4.246154], 'vp_lat': 50.1215, 'vp_lon': 8.7405}, {'node': '217.243.20.18', 'min_rtt': 0.842142, 'rtt_list': [0.967077, 0.842142, 1.577962], 'vp_lat': 50.1095, 'vp_lon': 8.6785}, {'node': '207.226.224.236', 'min_rtt': 0.908254, 'rtt_list': [0.930244, 0.908254, 19.555165], 'vp_lat': 50.1095, 'vp_lon': 8.7015}, {'node': '2.58.52.152', 'min_rtt': 0.925005, 'rtt_list': [2.579542, 1.126578, 0.925005], 'vp_lat': 50.1095, 'vp_lon': 8.6785}, {'node': '46.101.130.201', 'min_rtt': 0.963505, 'rtt_list': [1.097228, 0.963505, 0.991097], 'vp_lat': 50.1205, 'vp_lon': 8.7405}, {'node': '185.138.143.34', 'min_rtt': 1.124021, 'rtt_list': 

available measurements for ip: 684
[{'node': '95.47.236.146', 'min_rtt': 0.544513, 'rtt_list': [0.72565, 0.544513, 0.593419], 'vp_lat': 59.4595, 'vp_lon': 24.6875}, {'node': '212.7.0.250', 'min_rtt': 0.653659, 'rtt_list': [0.829155, 0.783692, 0.653659], 'vp_lat': 59.4615, 'vp_lon': 24.6895}, {'node': '212.3.202.246', 'min_rtt': 5.369891, 'rtt_list': [5.412925, 5.369891, 5.387996], 'vp_lat': 56.9675, 'vp_lon': 24.1695}, {'node': '46.183.219.225', 'min_rtt': 7.095253, 'rtt_list': [7.418754, 7.146529, 7.095253], 'vp_lat': 56.9515, 'vp_lon': 24.1115}, {'node': '86.38.3.141', 'min_rtt': 10.575957, 'rtt_list': [10.582309, 10.615735, 10.575957], 'vp_lat': 54.6875, 'vp_lon': 25.2205}, {'node': '213.197.128.134', 'min_rtt': 10.636048, 'rtt_list': [10.662757, 10.689987, 10.636048], 'vp_lat': 54.6405, 'vp_lon': 25.3075}, {'node': '213.108.25.10', 'min_rtt': 11.1669, 'rtt_list': [11.235136, 11.211551, 11.1669], 'vp_lat': 59.2975, 'vp_lon': 18.0895}, {'node': '5.20.2.255', 'min_rtt': 11.709261, 'rt

available measurements for ip: 686
[{'node': '185.118.112.5', 'min_rtt': 0.715245, 'rtt_list': [0.897466, 0.753574, 0.715245], 'vp_lat': 38.7205, 'vp_lon': -9.1395}, {'node': '31.14.143.132', 'min_rtt': 1, 'rtt_list': [52.211092, 1, 52.139936, 1, 52.052621, 1], 'vp_lat': 43.4615, 'vp_lon': 11.8375}, {'node': '185.39.208.23', 'min_rtt': 1.180391, 'rtt_list': [3.115916, 6.815415, 1.180391], 'vp_lat': 38.7175, 'vp_lon': -9.1395}, {'node': '5.182.48.97', 'min_rtt': 2.311622, 'rtt_list': [2.311622, 2.475058, 2.542646], 'vp_lat': 38.6575, 'vp_lon': -9.0805}, {'node': '156.154.79.254', 'min_rtt': 7.393818, 'rtt_list': [7.604053, 7.56212, 7.393818], 'vp_lat': 40.4475, 'vp_lon': -3.5685}, {'node': '92.38.171.55', 'min_rtt': 9.676424, 'rtt_list': [16.644769, 9.777266, 9.676424], 'vp_lat': 40.5815, 'vp_lon': -3.5795}, {'node': '147.84.200.125', 'min_rtt': 16.095827, 'rtt_list': [16.095827, 16.165808, 16.287829], 'vp_lat': 37.9905, 'vp_lon': -1.1285}, {'node': '185.233.100.99', 'min_rtt': 22.04377

available measurements for ip: 683
[{'node': '200.94.183.170', 'min_rtt': 0.735617, 'rtt_list': [0.73905, 0.735617, 1.256999], 'vp_lat': 25.7805, 'vp_lon': -100.1825}, {'node': '149.248.18.65', 'min_rtt': 33.453698, 'rtt_list': [33.453698, 33.514606, 33.591429], 'vp_lat': 34.0615, 'vp_lon': -118.2385}, {'node': '63.218.212.242', 'min_rtt': 33.604461, 'rtt_list': [33.610197, 33.641688, 33.604461], 'vp_lat': 34.0475, 'vp_lon': -118.2625}, {'node': '151.139.52.113', 'min_rtt': 36.758263, 'rtt_list': [36.805839, 36.831786, 36.758263], 'vp_lat': 32.7985, 'vp_lon': -96.8215}, {'node': '23.131.160.206', 'min_rtt': 41.419602, 'rtt_list': [41.707305, 41.419602, 41.798419], 'vp_lat': 37.4675, 'vp_lon': -121.9185}, {'node': '79.110.170.42', 'min_rtt': 41.477441, 'rtt_list': [41.600588, 41.477441, 41.480048], 'vp_lat': 37.4685, 'vp_lon': -121.9215}, {'node': '149.28.210.233', 'min_rtt': 41.611055, 'rtt_list': [41.713444, 41.647837, 41.611055], 'vp_lat': 37.3315, 'vp_lon': -121.8885}, {'node': '149

available measurements for ip: 684
[{'node': '92.243.9.77', 'min_rtt': 0.259968, 'rtt_list': [2.043944, 0.421898, 0.259968], 'vp_lat': 48.9275, 'vp_lon': 2.3485}, {'node': '195.80.157.38', 'min_rtt': 0.354836, 'rtt_list': [1.353162, 1.394258, 0.354836], 'vp_lat': 48.9275, 'vp_lon': 2.3505}, {'node': '199.247.13.129', 'min_rtt': 0.55913, 'rtt_list': [0.588535, 0.55913, 0.788236], 'vp_lat': 48.9095, 'vp_lon': 2.3705}, {'node': '89.185.60.124', 'min_rtt': 0.650531, 'rtt_list': [1.217202, 0.650531, 0.665202], 'vp_lat': 48.9305, 'vp_lon': 2.3495}, {'node': '80.67.163.251', 'min_rtt': 0.916298, 'rtt_list': [1.033369, 0.997503, 0.916298], 'vp_lat': 48.8585, 'vp_lon': 2.3785}, {'node': '178.250.7.79', 'min_rtt': 0.939039, 'rtt_list': [0.939039, 0.981038, 0.951863], 'vp_lat': 48.8585, 'vp_lon': 2.3875}, {'node': '85.118.58.213', 'min_rtt': 1.007612, 'rtt_list': [1.007612, 1.210108, 1.33905], 'vp_lat': 48.7805, 'vp_lon': 2.3795}, {'node': '217.25.179.62', 'min_rtt': 1.023417, 'rtt_list': [1.3260

...

available measurements for ip: 682
[{'node': '217.243.179.215', 'min_rtt': 0.424877, 'rtt_list': [0.432474, 0.588249, 0.424877], 'vp_lat': 48.1875, 'vp_lon': 16.3895}, {'node': '94.136.2.190', 'min_rtt': 0.42552, 'rtt_list': [0.665296, 0.550526, 0.42552], 'vp_lat': 48.2095, 'vp_lon': 16.3585}, {'node': '92.60.13.86', 'min_rtt': 0.483771, 'rtt_list': [1.57742, 0.483771, 0.489037], 'vp_lat': 48.2095, 'vp_lon': 16.3775}, {'node': '193.170.114.242', 'min_rtt': 0.507842, 'rtt_list': [0.892532, 0.507842, 0.582114], 'vp_lat': 48.2695, 'vp_lon': 16.4085}, {'node': '193.171.255.2', 'min_rtt': 0.741484, 'rtt_list': [1.231312, 0.741484, 1.918825], 'vp_lat': 48.2085, 'vp_lon': 16.3695}, {'node': '185.229.88.69', 'min_rtt': 0.812433, 'rtt_list': [0.919624, 0.812433, 0.833287], 'vp_lat': 48.1785, 'vp_lon': 16.3615}, {'node': '5.1.66.5', 'min_rtt': 1.007909, 'rtt_list': [1.017548, 1.007909, 1.00969], 'vp_lat': 48.1905, 'vp_lon': 16.3515}, {'node': '80.80.254.254', 'min_rtt': 4.498089, 'rtt_list': [4.

available measurements for ip: 683
[{'node': '103.62.48.193', 'min_rtt': 44.802633, 'rtt_list': [44.827082, 44.802633, 44.85053], 'vp_lat': 1.3005, 'vp_lon': 103.7875}, {'node': '203.119.15.254', 'min_rtt': 44.915713, 'rtt_list': [44.915713, 45.008218, 44.950317], 'vp_lat': 1.3005, 'vp_lon': 103.7915}, {'node': '103.84.153.114', 'min_rtt': 44.973653, 'rtt_list': [45.192405, 45.003101, 44.973653], 'vp_lat': 1.3005, 'vp_lon': 103.7915}, {'node': '103.116.125.2', 'min_rtt': 45.028068, 'rtt_list': [45.20597, 45.064239, 45.028068], 'vp_lat': 1.2985, 'vp_lon': 103.7915}, {'node': '203.175.175.206', 'min_rtt': 45.218081, 'rtt_list': [45.413697, 45.218081, 45.314831], 'vp_lat': 1.3205, 'vp_lon': 103.9205}, {'node': '103.148.239.134', 'min_rtt': 45.275058, 'rtt_list': [45.322192, 45.275058, 45.520273], 'vp_lat': 1.3505, 'vp_lon': 103.8205}, {'node': '139.162.3.33', 'min_rtt': 45.316035, 'rtt_list': [45.359807, 45.346224, 45.316035], 'vp_lat': 1.3215, 'vp_lon': 103.8875}, {'node': '139.180.132.3

available measurements for ip: 687
[{'node': '85.187.20.236', 'min_rtt': 28.495383, 'rtt_list': [28.713363, 28.518505, 28.495383], 'vp_lat': 42.6685, 'vp_lon': 23.3975}, {'node': '185.32.187.161', 'min_rtt': 29.656766, 'rtt_list': [29.661191, 29.656766, 29.711289], 'vp_lat': 55.6495, 'vp_lon': 37.5305}, {'node': '37.252.254.142', 'min_rtt': 29.90577, 'rtt_list': [29.961897, 29.90577, 29.938842], 'vp_lat': 55.8915, 'vp_lon': 37.5085}, {'node': '195.91.164.68', 'min_rtt': 30.020989, 'rtt_list': [30.210645, 30.175457, 30.020989], 'vp_lat': 55.7275, 'vp_lon': 37.6215}, {'node': '95.163.252.10', 'min_rtt': 30.198497, 'rtt_list': [30.256891, 30.226952, 30.198497], 'vp_lat': 55.7595, 'vp_lon': 37.6185}, {'node': '46.17.200.235', 'min_rtt': 30.639179, 'rtt_list': [30.639179, 30.704781, 30.759482], 'vp_lat': 55.7275, 'vp_lon': 37.6695}, {'node': '185.32.187.169', 'min_rtt': 39.434716, 'rtt_list': [39.434716, 39.542966, 39.632004], 'vp_lat': 59.8875, 'vp_lon': 30.3315}, {'node': '94.242.1.50', '

available measurements for ip: 685
[{'node': '172.93.18.42', 'min_rtt': 1.834406, 'rtt_list': [1.878737, 1.834406, 1.867921], 'vp_lat': 45.5185, 'vp_lon': -73.5215}, {'node': '35.203.43.169', 'min_rtt': 2.033524, 'rtt_list': [2.101148, 2.033524, 2.131444], 'vp_lat': 45.4975, 'vp_lon': -73.5725}, {'node': '155.254.2.42', 'min_rtt': 7.181977, 'rtt_list': [7.181977, 7.185105, 7.220949], 'vp_lat': 43.4775, 'vp_lon': -80.5495}, {'node': '149.248.50.86', 'min_rtt': 7.266915, 'rtt_list': [7.339886, 7.266915, 7.337929], 'vp_lat': 43.6505, 'vp_lon': -79.3605}, {'node': '23.159.16.30', 'min_rtt': 7.325416, 'rtt_list': [7.445086, 7.353238, 7.325416], 'vp_lat': 43.6515, 'vp_lon': -79.3785}, {'node': '207.167.121.7', 'min_rtt': 7.481041, 'rtt_list': [7.578421, 7.481041, 7.672671], 'vp_lat': 43.6515, 'vp_lon': -79.3585}, {'node': '103.144.177.30', 'min_rtt': 7.918186, 'rtt_list': [7.955416, 7.918186, 8.228894], 'vp_lat': 43.7675, 'vp_lon': -79.3295}, {'node': '128.100.103.40', 'min_rtt': 8.042101, '

available measurements for ip: 679
[{'node': '37.252.245.94', 'min_rtt': 0.380104, 'rtt_list': [1.46847, 0.582651, 0.380104], 'vp_lat': 25.0285, 'vp_lon': 55.1915}, {'node': '185.34.2.114', 'min_rtt': 0.447378, 'rtt_list': [0.510514, 0.447378, 0.5317], 'vp_lat': 25.6315, 'vp_lon': 55.8115}, {'node': '94.203.76.219', 'min_rtt': 2.687848, 'rtt_list': [2.809982, 2.687848, 2.689781], 'vp_lat': 25.0285, 'vp_lon': 55.1905}, {'node': '156.154.53.254', 'min_rtt': 2.984397, 'rtt_list': [2.984397, 3.000515, 2.985054], 'vp_lat': 25.1295, 'vp_lon': 56.3395}, {'node': '94.207.43.2', 'min_rtt': 4.599793, 'rtt_list': [4.63148, 4.599793, 4.606359], 'vp_lat': 25.0295, 'vp_lon': 55.1915}, {'node': '87.201.194.242', 'min_rtt': 7.401467, 'rtt_list': [7.493357, 7.462833, 7.401467], 'vp_lat': 25.0915, 'vp_lon': 55.1515}, {'node': '91.201.7.243', 'min_rtt': 10.3905, 'rtt_list': [11.557613, 10.3905], 'vp_lat': 24.4475, 'vp_lon': 54.3805}, {'node': '94.77.252.90', 'min_rtt': 12.728015, 'rtt_list': [12.871613, 

## output metrics

In [15]:
from geoloc_imc_2023.helpers import distance

geoloc_out_file = Path(".") / "../results/all_anchors_towards_all_anchors_geoloc.pickle"
with open(geoloc_out_file, "rb") as f:
    geoloc_results = pickle.load(f)


for i, target_addr in enumerate(geoloc_results):
    if i > 15: break
    target_lat = anchors[target_addr]["latitude"]
    target_lon = anchors[target_addr]["longitude"]

    estimated_lat = geoloc_results[target_addr]["estimated_lat"]
    estimated_lon = geoloc_results[target_addr]["estimated_lon"]

    d_error = distance(target_lat, estimated_lat, target_lon, estimated_lon)
    print(f"geoloc results for target ip: {target_addr} distance error: {d_error}")

geoloc results for target ip: 194.50.92.201 distance error: 0.11119492664426889
geoloc results for target ip: 195.43.87.140 distance error: 3.484385749573439
geoloc results for target ip: 185.32.189.249 distance error: 8.047647848051007
geoloc results for target ip: 200.94.182.170 distance error: 1.1672420891658457
geoloc results for target ip: 156.154.78.254 distance error: 0.21916969900161332
geoloc results for target ip: 195.158.60.23 distance error: 82.8489280458488
geoloc results for target ip: 217.197.95.69 distance error: 9.75821534068244
geoloc results for target ip: 5.188.108.64 distance error: 12.459106768061472
geoloc results for target ip: 45.76.126.106 distance error: 0.8943326443410874
geoloc results for target ip: 178.255.156.202 distance error: 0.2546820273647379
geoloc results for target ip: 54.39.185.31 distance error: 36.99168994011467
